In [ ]:
import agh_db_lectures

# Relational Database Design

## Key Types

In [ ]:
agh_db_lectures.nw_diagram.download_open()

- superkey
- candidate key
- primary key
- foreign key

_notes_

**Superkey** is a set of attributes whose values uniquely identify each tuple in a relation.  The `supplier_id` attributes itself forms a superkey of the `suppliers` relation.  But every superset of `{supplier_id}` (e.g., `{supplier_id, city}`) is also a superkey.

For now, we can use our knowledge of the world and the business to tell whether something is a superkey.

**Candidate key** is a minimal superkey, e.g., one that cannot have any attribute removed or it will no longer be a superkey.

**Primary key** is one of the candidate keys selected by DB schema designer to use for identifying tuples in a relation.

**Foreign key** is a set of attributes in a relation that are used to reference the primary key of another relation.  The foreign key attributes must be of the same types as the target primary key attributes.

For each tuple in a relation with a foreign key there has to be a tuple in the referened relation that has the same values of primary key attributes (unless foreign key contains `NULL`s).

Look for sample keys of all kinds in the Northwind db schema.

## Entity Relationship Model

With examples featuring a model of a (git) source code hosting platform, like [Codeberg](https://codeberg.org/) or GitLab.

_notes_

So far we've been working with databases using moderately low-level abstractions.  Tables and rows are sometimes called a logical model of the database.  They are specific to the relational data model and somewhat specific to the DBMS in use (for example, a Postgres DB schema might use the unsigned type `SERIAL` for a table column, whereas other DMBS might lack support for such data type).

When designing a database schema, we might start with a conceptual model, like the **entity-relationship model**, instead.  Such a model can make it easier to comprehend a large design and it also might (or might not, depending who you work with) represent business data relationships in a way closer to how people on nontechnical positions think of them.

There are various diagram notations for the ER model.  The notation of Peter Chen is the most popular and will be (more or less loosely) followed.

An **entity set**.

![](er-model-entity-set-example.svg)

_notes_

We shall define **entity** as an element of the world that we want to model.  A person, product, article, purchase, etc. can be an entity.  We represent an **entity set** ("type" in some literature) with a rectangle.

An entity can have **attributes**.  E.g., an `ACCOUNT` entity (being, e.g., a git forge account) can have an `EMAIL` attribute associated with it.  Attributes of an entity set (the "attribute types" in some more formal literature) are represented with ellipses.

An attribute (type) can have a domain — the set of allowed values of that attribute.  For example, a set of valid email addresses.  A special value `null` can also belong to some attribute's domain.  Even though domains are often mentioned when discussing the ER model, they are not represented on the diagrams.

A subset of entity set attributes should be selected that uniquely identifies each entity.  It is called the primary key.  Attibutes that are part of the primary key (key attributes) are represented with underlined attribute name.

The ER model permits modeling attributes that are **derived** from other attributes.  For example, the age of an account can be computed from the registration date.  It is a derived attribute.  We represent it with an ellipse with a dashed outline.

The ER model also permits modeling attributes that can have multiple values.  For example, a git forge account can have multiple SSH keys configured in order to authenticate from multiple devices.  The number of SSH keys would vary between the `ACCOUNT` entities.  We can represent SSH keys as a **multivalued** attribute, with double outline on the diagram.

An attribute can also be **composite**, meaning it is further broken into parts.  E.g., the `LOGIN_DATA` of an `ACCOUNT` entity can be a composite attribute consisting of `PASSWORD_HASH` and `SALT`.  We could also make the parts themselves composite.  Perhaps it would make sense to represent `SALT` as consiting of algorithms type, iterations count and random data?  Nonetheless, an authentication API used by an application is likely to accept the entire `LOGIN_DATA` of an `ACCOUNT` as a single string-valued argument.

Entities can form relationships.  For example, en `ACCOUNT` entity could be in a membership relationship with a `GROUP` entity.  Consider groups like [guix](https://codeberg.org/guix) on Codeberg.  Since we work with the notion of entity sets and multiple entities can be in multiplem membership relationships, we shall talk about **relationship sets**.  A relationship set is going to be represented with a diamond.

A **many-to-many** mapping.

![](many-to-many.svg)

_notes_

A single `ACCOUNT` entity can be in a membership relationship with zero, one, or multiple `GROUP` entities.  Also, multiple `ACCOUNT` entities can be in a relationship with a single `GROUP` entity.  There can be many entities on each side of the relationship set, so we say it has a **many-to-many** cardinality.  There can also exist relationship sets with **one-to-one**, **one-to-many**, and **many-to-one** cardinalities.  The **cardinality** can be represented on the diagram with annotations like `1`, or `0..n`.  Some other common notations are just `n` or an asterisk (`*`) for the "many" side of a relationship set.

If we wanted each group to have a single owner (aka admin), the relationship set of group ownership could be modeled with many-to-one mapping cardinality.  If, for some reason, we were to require that each user owns at most one group, that could modeled with a one-to-one mapping.

_notes_

Entity set participates **totally** in a relationship set if every entity **has to** be in some relationship from the set.  Otherwise, it is participates **partially**.

Notice that groups on a git forge could own code repositories (Codeberg works like this).  We can include an entity set `REPOSITORY` in our model.  Note that even though it has an attribute `REPO_NAME`, it is insufficient to uniquely identify all repositories on the forge.  Multiple groups can have repositories with the same name (like there are multiple repositories named "guix" on Codeberg).

If an entity set does not have enough attributes to form a key, we say that it is **weak**.  A weak entity set has to participate in a relationship set with another entity set (or multiple other entity sets…) that is not weak (i.e., is **strong**).  We use the notions of an **identifying relationship**, and an **identifying entity set**.  In the weak entity set we designate a subset of attributes called the **discriminator**.  Together with the primary key of the identifying entity set, the discriminator forms the primary key of the weak entity set.  The weak entity and its identifying relationship set are going to be represented with double outlines on the diagrams.  A weak entity could of course additionally participate in other relationship sets that are not used to identify it (and are thus **not** represented with a double outline).

An entity can be in a relationship with another entity of the same type.  As in case of the `FOLLOWS` relationship set (which is a **recursive** relationship set).  To distinguish between the left-side and right-side participation, we can **name the roles** of entities on each side (e.g., `follower` and `followed`).

Finally, a relationship set can have attributes of its own.  We can add a `MEMBERSHIP_DATE` attribute to the relationship set is we want to record when someone has joined given group.

![](er-model-example.svg)

_notes_

A ternary (or higher degree) relationship can occur between 3 (or more) entities.  Here we used it to record who added each account to group.  It is a minor detail that 2 sides of this ternary relationship set happen to invole the same entity set — an n-ary relationship set can just as well involve distinct entity sets.

It is impossible to model it correctly by just binary relationship sets between the entity sets that we already have.  However, it would be possible to model it correctly with a weak entity set identified jointly by three other entity sets.

## Enhanced Entity Relationship Model

EER model builds upon Peter Chen's ER model and adds specialization/generalization (described here) as well as aggregation (not covered).

![](eer-model-example.svg)

_notes_

A typical git forge would allow both groups **and** accounts to own repositories.  As such, the `ACCOUNT` and `GROUP` entity types could be thought of as **specializations** of another entity type that we could call `NAMESPACE_HOLDER` (since we typically refer to repositories as `https://some-forge.org/namespace_name/repo_name`).

We could also say that our `NAMESPACE_HOLDER` entity type is a **generalization** of the other two types.  Whether we talk about specialization or generalization depends on whether we think top-down or bottom-up.

Specialization is similar to inheritance in object-oriented programming languages.  A entity type that is a specialization of another type **inherits** its attributes, possibly also including some additional attributes of its own.

Specialization can be represented with line going from an entity set to a circle and other lines going from the circle to the specializations.  The lines that go to specializations are crossed with arcs, as shown in the diagram.  Multi-level specialization/generalization hierarchies can be used.

A specialization is **disjoint** if each entity is a member of at most one specialized type.  It is **overlapping** if an entity can be a member of multiple specialized types.  We denote it with letter "d" or "o" inside the circle.

A specialization is **total** if each higher-level entity has to be a member of some specialized type.  It is **partial** if we allow higher-level entities not to be members of any specialized type.  We denote it with letter "t" or "p" along the line going from higher-level entity set to the circle.

Aggregation and **categorization** (aka multiple inheritance) are also used in EER model but are not going to be covered here.

## Notes on (E)ER modeling

_notes_

Theodore, are there any reasons not to represent the `SSH_KEY` as another entity set rather than a multivalued attribute?

There isn't always a rule whether to use a new entity type or a multivalued attribute (or a ternary relationship set).  "Good taste" is needed.

There can be multiple valid choices for a primary key.  Also, one might choose to introduce an additional number (identifier) attribute to some entity set and use it in the primary key.

**Do not** include primary key attributes of some entity as attributes of some other entity in order to make a "foreign key".  There are no foreign keys in the (E)ER model, use relationship sets instead :)

A workflow can be as follows.

- entity sets identification
- relationship sets identification
- deciding on cardinality of relationship sets' mappings
- identification of entity set attributes
- primary key selection
- identification of weak entity sets and their identifying relationship sets and identifying entity sets
- identification of weak entity sets' discriminators
- abstractions
  - specialization/generalization,
  - aggregation, and
  - categorization
- determining whether the abstractions are
  - total/partial, and
  - disjoin/overlapping

## Mapping the Conceptual (E)ER Model to Relational Model

We shall give some examples but omit formal algorithm descriptions.

#### Entity Sets and Attributes

![](er-model-entity-w-attributes.svg)

-----------------------------

![](er-model-entity-w-attributes-mapped.svg)

_notes_

Entity set gets mapped to a relation. Ordinary attributes become relation attributes.

Multivalued attributes get their own relations.

Derived attributes are absent in relation schema.

Note how we mark primary keys and foreign key constraints in schema diagram.  Be aware that different notations are in use.  See the WP database schema for another common way to mark cardinalities.

#### Entity Relationships and Weak Entity Types

![](er-model-example.svg)

-----------------------------

![](er-model-mapped.svg)

#### Generalization / Specialization

![](eer-model-example.svg)

-----------------------------

![](eer-model-mapped.svg)

_notes_

Alternative approach is to have just one relation for all specialized types with the attributes of all specializations present there and nullable.

## Schema Normalization

Let's formalize:

#### Relation Schema

$some\_relation({attribute_1, attribute_2, attribute_3})$

#### Relation Instance

<table>
  <thead>
    <tr>
      <th style="text-align: center">attribute_1</th>
      <th style="text-align: center">attribute_2</th>
      <th style="text-align: center">attribute_3</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">4</td>
      <td style="text-align: center">12.43</td>
    </tr>
    <tr>
      <td style="text-align: center">1345</td>
      <td style="text-align: center">4</td>
      <td style="text-align: center">3.19</td>
    </tr>
    <tr>
      <td style="text-align: center">1564</td>
      <td style="text-align: center">8</td>
      <td style="text-align: center">17.03</td>
    </tr>
  </tbody>
</table>

_notes_

Schema is a design of relation (or entire database) structure, including integrity constraints.

Instance is a data snapshot of a relation at given point in time.

### The Use-Case of Normalization

Assume another relation schema was designed to store information about issues and comments under them.

$R = \{issue\_number, repo\_name, owner\_name, issue\_text, comment\_id, comment\_text\}$

$issue\_comment(R)$

_notes_

Such relation schema could be, for example, the result of ad-hoc design.  We deliberately make the example small by, e.g., omitting authorship information.

Consider an instance of this relation with some data.

<table>
  <thead>
    <tr>
      <th style="text-align: center">issue_number</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">issue_text</th>
      <th style="text-align: center">comment_id</th>
      <th style="text-align: center">comment_text</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">I get `bash: git: command not found` when trying to download this :(</td>
      <td style="text-align: center">9814</td>
      <td style="text-align: center">You need to install the git command.  E.g., with `apt install git`.</td>
    </tr>
    <tr>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">I get `bash: git: command not found` when trying to download this :(</td>
      <td style="text-align: center">9819</td>
      <td style="text-align: center">Works like a charm. Thanks!</td>
    </tr>
    <tr>
      <td style="text-align: center">1345</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">`librecad` package lacks icons and .desktop files from the upstream project at https://github.com/LibreCAD/LibreCAD.</td>
      <td style="text-align: center">10239</td>
      <td style="text-align: center">Fixed in 58b522a.</td>
    </tr>
  </tbody>
</table>

_notes_

What are the problem with this relation schema?

- duplicate storage of `issue_text`
- need to be careful when updating it
- need to be careful when deleting an issue
- challenge of recording an issue that has no comments yet (`NULL` in `comment_*` columns?)

It is often said that a design suffers from **anomalies** of data modification.  Data redundancy is bad, mkay?

#### Decomposed Relation

$issue(issue\_number, repo\_name, owner\_name, issue\_text)$

$comment(comment\_id, issue\_number, comment\_text)$

<table>
  <thead>
    <tr>
      <th style="text-align: center">issue_number</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">issue_text</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">I get `bash: git: command not found` when trying to download this :(</td>
    </tr>
    <tr>
      <td style="text-align: center">1345</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">`librecad` package lacks icons and .desktop files from the upstream project at https://github.com/LibreCAD/LibreCAD.</td>
    </tr>
  </tbody>
</table>

<table>
  <thead>
    <tr>
      <th style="text-align: center">comment_id</th>
      <th style="text-align: center">issue_number</th>
      <th style="text-align: center">comment_text</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">9814</td>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">You need to install the git command.  E.g., with `apt install git`.</td>
    </tr>
    <tr>
      <td style="text-align: center">9819</td>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">Works like a charm. Thanks!</td>
    </tr>
    <tr>
      <td style="text-align: center">10239</td>
      <td style="text-align: center">1345</td>
      <td style="text-align: center">Fixed in 58b522a.</td>
    </tr>
  </tbody>
</table>

_notes_

We can **decompose** relation schemas with data redundancy into smaller relation schemas that do not suffer from this problem.

The resulting tables here would be joinable on the `issue_number` attribute.  No information would be lost.

#### Lossy Decomposition

$issue(issue\_number, repo\_name, owner\_name, issue\_text)$

$comment(comment\_id, repo\_name, owner\_name, comment\_text)$


<table>
  <thead>
    <tr>
      <th style="text-align: center">issue_number</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">issue_text</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">1112</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">I get `bash: git: command not found` when trying to download this :(</td>
    </tr>
    <tr>
      <td style="text-align: center">1345</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">`librecad` package lacks icons and .desktop files from the upstream project at https://github.com/LibreCAD/LibreCAD.</td>
    </tr>
  </tbody>
</table>

<table>
  <thead>
    <tr>
      <th style="text-align: center">comment_id</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">comment_text</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">9814</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">You need to install the git command.  E.g., with `apt install git`.</td>
    </tr>
    <tr>
      <td style="text-align: center">9819</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">Works like a charm. Thanks!</td>
    </tr>
    <tr>
      <td style="text-align: center">10239</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">Fixed in 58b522a.</td>
    </tr>
  </tbody>
</table>

_notes_

Such decomposed schema is broken — it doesn't keep the information about the precise issue that a comment has been made under.  There could possibly be multiple issues opened for the same repo.

Decomposition is **lossy** if it loses information.

_notes_

Decomposition is **lossless** if and only if a natural join of decomposed smaller relations gives back the original relation.

## 1NF

First normal form.

<table>
  <thead>
    <tr>
      <th style="text-align: center">user_name</th>
      <th colspan="2" style="text-align: center">privileges</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">repo_owner_name</th>
    </tr>
    <tr>
      <th style="text-align: center"></th>
      <th style="text-align: center">branch_name</th>
      <th style="text-align: center">access_type</th>
      <th style="text-align: center"></th>
      <th style="text-align: center"></th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td rowspan="3" style="text-align: center">theodore</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td rowspan="3" style="text-align: center">db-lecture-materials</td>
      <td rowspan="3" style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">join-diagram-wip</td>
      <td style="text-align: center">push</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore-experiments</td>
      <td style="text-align: center">forcepush</td>
    </tr>
    <tr style="border-top: 1px solid black">
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr style="border-top: 1px solid black">
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
    <tr style="border-top: 1px solid black">
      <td style="text-align: center">eugenia</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
  </tbody>
</table>

_notes_

A relation is in 1NF if it has no multivalued nor composite attributes.  Note that many RDBMS engines do not even have dedicated support for such attributes.  Others do.  For example, Postgres features an array type, and SQL standard since 2003 specifies an XML type.

Depending on the semantic of data, a single string-valued attribute can be effetively composite (or multivalued).  One example is the `user_pass` attribute in WP database that holds both the password hash and the salt in a single string.

The above is not in 1NF.

### Decomposition to 1NF

<table>
  <thead>
    <tr>
      <th style="text-align: center">user_name</th>
      <th style="text-align: center">branch_name</th>
      <th style="text-align: center">access_type</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">repo_owner_name</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">join-diagram-wip</td>
      <td style="text-align: center">push</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">theodore-experiments</td>
      <td style="text-align: center">forcepush</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
    <tr>
      <td style="text-align: center">eugenia</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
  </tbody>
</table>

## Functional Dependencies

$a, b, c, d, e$ — relation attributes

$\{a, b\} \rightarrow \{c, d\}$

_notes_

Functional dependencies between relation attributes can be used to approach the issue of normalization in a formal way.

We will use arrow notation.

Functional dependency means that values of LHS attributes uniquely determine the values of RHS attributes.

Assume the following relation.

$r(a, b, c, d, e)$

$t_1, t_2$ — tuples of a relation instance

The functional dependency $\{a, b\} \rightarrow \{c, d\}$ means that:

$(t_1[a], t_1[b]) = (t_2[a], t_2[b]) \implies (t_1[c], t_1[d]) = (t_2[c], t_2[d])$

_notes_

I.e., if we know the values of LHS attributes, we could tell what the RHS attribute values are.

We can say that a relation instance **satisfies** a functional dependency.  If all legal instances of a relation do so, then the functional dependency **holds** on schema.

<table>
  <thead>
    <tr>
      <th style="text-align: center">a</th>
      <th style="text-align: center">b</th>
      <th style="text-align: center">c</th>
      <th style="text-align: center">d</th>
      <th style="text-align: center">e</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">1</td>
      <td style="text-align: center">1</td>
      <td style="text-align: center">13</td>
      <td style="text-align: center">5.67</td>
      <td style="text-align: center">24</td>
      </tr>
    <tr>
      <td style="text-align: center">1</td>
      <td style="text-align: center">1</td>
      <td style="text-align: center">13</td>
      <td style="text-align: center">5.67</td>
      <td style="text-align: center">24</td>
      </tr>
    <tr>
      <td style="text-align: center">2</td>
      <td style="text-align: center">1</td>
      <td style="text-align: center">43</td>
      <td style="text-align: center">0.43</td>
      <td style="text-align: center">11</td>
      </tr>
    <tr>
      <td style="text-align: center">2</td>
      <td style="text-align: center">2</td>
      <td style="text-align: center">54</td>
      <td style="text-align: center">15.53</td>
      <td style="text-align: center">0</td>
      </tr>
    <tr>
      <td style="text-align: center">2</td>
      <td style="text-align: center">2</td>
      <td style="text-align: center">54</td>
      <td style="text-align: center">15.53</td>
      <td style="text-align: center">9</td>
      </tr>
  </tbody>
</table>

_notes_

Relation instance presented above satisfies the functional dependency we are considering.

Change the value of `c` in the last row to 77.  The new instance does not satisfy the functional dependency.

#### Examples From the Git Forge Schema

$name \rightarrow email$

$\{added, group\_name\} \rightarrow adder$

_notes_

LHS and RHS of a functional dependency are **sets** of attributes but we can abuse the notation and drop the braces when we have just one attribute.

#### Trivial Functional Dependencies

$\{added, group\_name\} \rightarrow group\_name$

#### Armstrong's Axioms

$\alpha, \beta, \gamma$ — attribute sets

$\alpha\gamma$ — simplified notation for $\alpha{\cup}\gamma$

The axioms are:

$\beta{\subseteq}\alpha \implies \alpha \rightarrow \beta$

$\alpha \rightarrow \beta \implies \alpha\gamma \rightarrow \beta\gamma$

$\alpha \rightarrow \beta \land \beta \rightarrow \gamma \implies \alpha \rightarrow \gamma$

_notes_

Functional dependencies can logically imply other functional dependencies.  A set $F^+$ of all functional dependencies implied by set $F$ is called **closure**.  Armstrong's axioms allow finding the closure of every set of functional dependencies.

Other tautologies can be proved from these axioms.

#### Implied Functional Dependencies Example

We have the following functional dependencies.

$name \rightarrow email$

$email \rightarrow \{name, registration\_date, email, password\_hash, salt\}$

We can then prove the following as well.

$\{password\_hash, salt\} \rightarrow \{password\_hash, salt\}$

$name \rightarrow \{registration\_date, email\}$

_notes_

$\{password\_hash, salt\} \rightarrow \{password\_hash, salt\}$ is a trivial one.

## BCNF

Boyce-Codd Normal Form (also called 3.5 Normal Form).

Let

$R$ — set of relation attributes

$F$ — set of functional dependencies with attributes in $R$

$F^+$ — closure of $F$

A relation schema is in BCNF if and only if it is in 1NF, and

$\forall (\alpha \rightarrow \beta){\in}F^+: \beta{\subseteq}\alpha \lor \alpha\ is\ a\ superkey$

### BCNF Example

Consider again the following attributes and relation schema.

$R = \{issue\_number, repo\_name, owner\_name, issue\_text, comment\_id, comment\_text\}$

$issues\_comments(R)$

We have these (and more) functional dependencies.

$comment\_id \rightarrow comment\_text$

$comment\_id \rightarrow issue\_number$

$issue\_number \rightarrow \{repo\_name, owner\_name, issue\_text\}$

_notes_

We won't be writing down all the other functional dependencies that result from these.  

The first two functional dependencies are OK wrt the BCNF requirements.

_notes_

`comment_id` is the primary key (and **the only** candidate key).

The last functional dependency

- is not trivial, and
- has LHS that is not a superkey.

Therefore, the dependency $issue\_number \rightarrow \{repo\_name, owner\_name, issue\_text\}$ violates BCNF.

_notes_

`issue_number` does not uniquely identify each tuple in the relation.

### Decomposition to BCNF Schemas

If we have a nontrivial functional dependency $\alpha \rightarrow \beta$ that violates BCNF, then we can decompose the relation schema into two separate schemas:

$\alpha{\cup}\beta$

$R{-}(\beta{-}\alpha)$

In our case:

$R = \{issue\_number, repo\_name, owner\_name, issue\_text, comment\_id, comment\_text\}$

$\alpha = issue\_number$

$\beta = \{repo\_name, owner\_name, issue\_text\}$

We get the following decomposed relation schemas.

$issue(\alpha{\cup}\beta) = issue(issue\_number, repo\_name, owner\_name, issue\_text)$

$comment(R{-}(\beta{-}\alpha)) = comment(comment\_id, issue\_number, comment\_text)$

_notes_

Here this would give us the same decomposition we used earlier.

Note that merely checking if a database schema is in BCNF is an NP-complete problem.  We don't discuss the particular algorithms as part of this course.

### Dependency Preservation

Consider this schema, dependencies, and sample instance.

$repo\_role\_user(repo\_name, owner\_name, role\_id, user)$

$\{repo\_name, owner\_name, user\} \rightarrow role\_id$

$role\_id \rightarrow \{repo\_name, owner\_name\}$

<table>
  <thead>
    <tr>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">role_id</th>
      <th style="text-align: center">user</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">342</td>
      <td style="text-align: center">theodore</td>
    </tr>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">377</td>
      <td style="text-align: center">pancratius</td>
    </tr>
    <tr>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">392</td>
      <td style="text-align: center">pancratius</td>
    </tr>
    <tr>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">392</td>
      <td style="text-align: center">eugenia</td>
    </tr>
  </tbody>
</table>

_notes_

Assume a scenario where each repository can have multiple roles defined and users can have at most one role for each repository.  Role is repo-specific and defines privileges.

We have the following candidate keys.

$k_1 = \{repo\_name, owner\_name, user\}$

$k_2 = \{role\_id, user\}$

_notes_

Functional dependency $\{repo, user\} \rightarrow role\_id$ has a candidate key on its LHS.  It does not violate BCNF.

Functional dependency $role\_id \rightarrow \{repo\_name, owner\_name\}$ is not trivial and its LHS is not a superkey.  It does violate the BCNF.

We decompose according to our rule specified earlier.

$R = \{repo\_name, owner\_name, role\_id, user\}$

$\alpha = role\_id$

$\beta = \{repo\_name, owner\_name\}$

The following are new relation schemas and their sample instances.

$role\_repo(\alpha{\cup}\beta) = role\_repo(role\_id, repo\_name, owner\_name)$

$user\_role(R{-}(\beta{-}\alpha)) = user\_role(user, role\_id)$

<div style="display: flex">
<table>
  <thead>
    <tr>
      <th style="text-align: center">role_id</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">342</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">377</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">392</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
  </tbody>
</table>

<table>
  <thead>
    <tr>
      <th style="text-align: center">user</th>
      <th style="text-align: center">role_id</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">342</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">377</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">392</td>
    </tr>
    <tr>
      <td style="text-align: center">eugenia</td>
      <td style="text-align: center">392</td>
    </tr>
  </tbody>
</table>
</div>

Recall our functional dependency $\{repo\_name, owner\_name, user\} \rightarrow role\_id$.

_notes_

This dependency involves attributes that no longer appear together in any single relation schema.

We could no longer tell whether this dependency is satisfied by looking at a single relation instance.

We say this decomposition **is not dependency preserving**.  This is an undesirable situation.

Not all relation schemas have a dependency preserving decomposition to a set of BCNF shemas.

## 3NF

Third Normal Form.

Recall that a relation schema is in BCNF if and only if it is in 1NF, and

$\forall (\alpha \rightarrow \beta){\in}F^+: \beta{\subseteq}\alpha \lor \alpha\ is\ a\ superkey$

Let's relax the condition relating to dependencies.  Replace it with the following.

$\forall (\alpha \rightarrow \beta){\in}F^+: \beta{\subseteq}\alpha \lor \alpha\ is\ a\ superkey \lor \forall A{\in}(\beta-\alpha) \exists k{\in}K: A{\in}k\$

where

$K$ — set of relation's all candidate keys

_notes_

This is one of the possible, equivalent definitions of 3NF (not the canonical one).

3NF permits nonkey attributes on the LHS of a nontrivial functional dependency provided that the relevant attributes in the RHS belong to some candidate keys.  These attribute are not required to belong to the same candidate key, though.

### 3NF in the User Roles Example

Recall our earlier schema, dependencies and candidate keys.

$repo\_role\_user(repo\_name, owner\_name, role\_id, user)$

$\{repo\_name, owner\_name, user\} \rightarrow role\_id$

$role\_id \rightarrow \{repo\_name, owner\_name\}$

$k_1 = \{repo\_name, owner\_name, user\}$

$k_2 = \{role\_id, user\}$

We see that $repo\_name{\in}k_1$ and $owner\_name{\in}k_1$.

_notes_

The second functional dependency violates BCNF on $user\_repo\_role$ and leads to a decomposition that is not dependency preserving.

If we instead strive for 3NF, we shall see that this dependency does not violate it.  Dependency's RHS attributes all belong to a candidate key.  3NF does not require further decomposition of this schema.

3NF is weaker than BCNF and allows some degree of redundancy while preserving functional dependencies.

### Multivalued dependencies

Assume users can watch (aka subscribe to) others' repositories.  Consider this relation schema and sample instance.

$account(name, email, ssh\_key, watched\_repo\_name, watched\_repo\_owner)$

$name \rightarrow email$

$email \rightarrow name$

<table>
  <thead>
    <tr>
      <th style="text-align: center">name</th>
      <th style="text-align: center">email</th>
      <th style="text-align: center">watched_repo_name</th>
      <th style="text-align: center">watched_repo_owner</th>
      <th style="text-align: center">ssh_key</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">wkosior@agh.edu.pl</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…dyItC</span></td>
    </tr>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">wkosior@agh.edu.pl</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…ujdSO</span></td>
    </tr>
    <tr>
      <td style="text-align: center">wk-bot</td>
      <td style="text-align: center">wk-bot@gnu.org</td>
      <td style="text-align: center">apache-configs</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…ujdSO</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">543210@student.agh.edu.pl</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…T7EjR</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">543210@student.agh.edu.pl</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-rsa <span style="white-space: pre">AAAAB3…PucE=</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">543210@student.agh.edu.pl</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…T7EjR</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">543210@student.agh.edu.pl</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">ssh-rsa <span style="white-space: pre">AAAAB3…PucE=</span></td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">500000@student.agh.edu.pl</td>
      <td style="text-align: center">apache-configs</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-dss <span style="white-space: pre">AAAAB3…0yxM=</span></td>
    </tr>
  </tbody>
</table>

_notes_

A user can have multiple SSH keys and can be watching multiple repositories.  It's obviously wrong to store all these in a single relation, but let's hold on to this example just for a moment.

Please do not mind the omission of login data in the example and truncated display of SSH keys — this is to avoid making the table even wider.  Please also treat $ssh\_key$ as if it were an atomic attribute, even though we see a way to decompose it.

There's clearly no dependency between the SSH keys and watched repositories.  For each user we shall therefore repeat user's every SSH key with user's every watched repository, in separate rows / tuples.  As when computing a cartesian product.

Temporarily remove the 2 middle rows of Theodore.  Note that now the relation instance indicates some connection between Theodore's particular key and watched repository.  This is not what we want, so we need to get back to the cartesian-product-like instance.

Note that there are no nontrivial functional dependencies involving $ssh\_key$, $watched\_repo\_name$, and $watched\_repo\_owner$.

The relation schema, although bad, is in BCNF.  We have not yet learned any formal rule we could use to decompose it.

We have the following **multivalued dependencies**.

$name \twoheadrightarrow ssh\_key$

$name \twoheadrightarrow \{watched\_repo\_name, watched\_repo\_owner\}$

_notes_

The first dependency means that the value of $name$ is always associated with the same set of values of $ssh\_key$, regardless of the values of other attribtues.

The second dependency means that the value of $name$ is always associated with the same set of value tuples of $\{watched\_repo\_name, watched\_repo\_owner\}$, regardless of the values of other attributes.

Our instance satisfies both dependencies.  If we remove the middle 2 of Theodore's rows, it shall satisfy neither.

The mathematical notation for multivalued dependency constraint can be found in literature.

More could be derived, for example the following.

$email \twoheadrightarrow \{watched\_repo\_name, watched\_repo\_owner\}$

$\{ssh\_key, watched\_repo\_name\} \twoheadrightarrow ssh\_key$ — a trivial one

### 4NF

Fourth Normal Form.

Let

$R$ — set of relation attributes

$M^+$ — set of all functional **and** multivalued dependencies with attributes in $R$

A relation schema is in 4NF if and only if it is in BCNF, and

$\forall (\alpha \twoheadrightarrow \beta){\in}M^+: \beta{\subseteq}\alpha \lor \alpha{\cup}\beta = R \lor \alpha\ is\ a\ superkey$

_notes_

Note that every superkey of our sample relation schema must contain all three: $ssh\_key$, $watched\_repo\_name$, and $watched\_repo\_owner$.  Sample candidate key is $\{name, ssh\_key, watched\_repo\_name, watched\_repo\_owner\}$.

The dependency $name \twoheadrightarrow ssh\_key$ is not trivial and its LHS is not a superkey.

Similarly, the dependency $name \twoheadrightarrow \{watched\_repo\_name, watched\_repo\_owner\}$ is not trivial and its LHS is not a superkey.

The relation schema is in BCNF but it is not in 4NF.

### Decomposition to 4NF Schemas

If we have a nontrivial multivalued dependency $\alpha \twoheadrightarrow \beta$ that violates 4NF, then we can decompose the relation schema into two separate schemas:

$\alpha{\cup}\beta$

$R{-}(\beta{-}\alpha)$

_notes_

This is analogous to our rule of decomposition to BCNF schemas.

In our case:

$R = \{name, email, ssh\_key, watched\_repo\_name, watched\_repo\_owner\}$

$\alpha = name$

$\beta = ssh\_key$

We get the following decomposed relation schemas.

$account\_ssh\_key(\alpha{\cup}\beta) = account\_ssh\_key(name, ssh\_key)$

$account'(R{-}(\beta{-}\alpha)) = account'(name, email, watched\_repo\_name, watched\_repo\_owner)$

The $account'$ schema is still not in 4NF, so we can decompose it furter and get the following 4NF schemas and sample relation instances.

$account\_ssh\_key(name, ssh\_key)$

$account\_watch(name, watched\_repo\_name, watched\_repo\_owner)$

$account''(name, email)$

<table>
  <thead>
    <tr>
      <th style="text-align: center">name</th>
      <th style="text-align: center">email</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">wkosior@agh.edu.pl</td>
    </tr>
    <tr>
      <td style="text-align: center">wk-bot</td>
      <td style="text-align: center">wk-bot@gnu.org</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">543210@student.agh.edu.pl</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">500000@student.agh.edu.pl</td>
    </tr>
  </tbody>
</table>

<div style="display: flex">
<table>
  <thead>
    <tr>
      <th style="text-align: center">name</th>
      <th style="text-align: center">ssh_key</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…dyItC</span></td>
    </tr>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…ujdSO</span></td>
    </tr>
    <tr>
      <td style="text-align: center">wk-bot</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…ujdSO</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">ssh-ed25519 <span style="white-space: pre">AAAAC3…T7EjR</span></td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">ssh-rsa <span style="white-space: pre">AAAAB3…PucE=</span></td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">ssh-dss <span style="white-space: pre">AAAAB3…0yxM=</span></td>
    </tr>
  </tbody>
</table>
<table>
  <thead>
    <tr>
      <th style="text-align: center">name</th>
      <th style="text-align: center">watched_repo_name</th>
      <th style="text-align: center">watched_repo_owner</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">guix</td>
    </tr>
    <tr>
      <td style="text-align: center">wk-bot</td>
      <td style="text-align: center">apache-configs</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">guix</td>
        <td style="text-align: center">tim448352</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">apache-configs</td>
      <td style="text-align: center">wkosior</td>
    </tr>
  </tbody>
</table>
</div>

### Another 4NF Example

Consider this schema, dependencies, and sample instance.

$repo\_role\_user(repo\_name, owner\_name, role\_id, branch, privilege, user)$

$\{repo\_name, owner\_name, user\} \rightarrow role\_id$

$role\_id \rightarrow \{repo\_name, owner\_name\}$

$role\_id \twoheadrightarrow \{branch, privilege\}$

<table>
  <thead>
    <tr>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
      <th style="text-align: center">role_id</th>
      <th style="text-align: center">branch</th>
      <th style="text-align: center">privilege</th>
      <th style="text-align: center">user</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">342</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">theodore</td>
    </tr>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">342</td>
      <td style="text-align: center">join-diagram-wip</td>
      <td style="text-align: center">push</td>
      <td style="text-align: center">theodore</td>
    </tr>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">342</td>
      <td style="text-align: center">theodore-experiments</td>
      <td style="text-align: center">forcepush</td>
      <td style="text-align: center">theodore</td>
    </tr>
    <tr>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
      <td style="text-align: center">377</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">pancratius</td>
    </tr>
    <tr>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">392</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">pancratius</td>
    </tr>
    <tr>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
      <td style="text-align: center">392</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
      <td style="text-align: center">eugenia</td>
    </tr>
  </tbody>
</table>

We first decompose to the following BCNF schemas.

$user\_role(user, role\_id, branch, privilege)$

$role\_repo(role\_id, repo\_name, owner\_name)$

Then we further decompose to 4NF schemas.

$role\_repo(role\_id, repo\_name, owner\_name)$

$role(role\_id, branch, privilege)$

$user\_role'(user, role\_id)$

<table>
  <thead>
    <tr>
      <th style="text-align: center">role_id</th>
      <th style="text-align: center">branch</th>
      <th style="text-align: center">privilege</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">342</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
    </tr>
    <tr>
      <td style="text-align: center">342</td>
      <td style="text-align: center">join-diagram-wip</td>
      <td style="text-align: center">push</td>
    </tr>
    <tr>
      <td style="text-align: center">342</td>
      <td style="text-align: center">theodore-experiments</td>
      <td style="text-align: center">forcepush</td>
    </tr>
    <tr>
      <td style="text-align: center">377</td>
      <td style="text-align: center">magister</td>
      <td style="text-align: center">pull</td>
    </tr>
    <tr>
      <td style="text-align: center">392</td>
      <td style="text-align: center">trunk</td>
      <td style="text-align: center">pull</td>
    </tr>
  </tbody>
</table>

<div style="display: flex">
<table>
  <thead>
    <tr>
      <th style="text-align: center">role_id</th>
      <th style="text-align: center">repo_name</th>
      <th style="text-align: center">owner_name</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">342</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">377</td>
      <td style="text-align: center">db-lecture-materials</td>
      <td style="text-align: center">wkosior</td>
    </tr>
    <tr>
      <td style="text-align: center">392</td>
      <td style="text-align: center">guix</td>
      <td style="text-align: center">tim448352</td>
    </tr>
  </tbody>
</table>
<table>
  <thead>
    <tr>
      <th style="text-align: center">user</th>
      <th style="text-align: center">role_id</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td style="text-align: center">theodore</td>
      <td style="text-align: center">342</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">377</td>
    </tr>
    <tr>
      <td style="text-align: center">pancratius</td>
      <td style="text-align: center">392</td>
    </tr>
    <tr>
      <td style="text-align: center">eugenia</td>
      <td style="text-align: center">392</td>
    </tr>
  </tbody>
</table>
</div>

_notes_

These are relation instances that correspond to the initial instance.

### Notes on Database Design

_notes_

Other normal forms exist that are not covered here.

One can design a database by

- listing all needed relation attributes and relevant dependencies and normalizing the design starting with a single big relation,
- creating an (E)ER model and mapping it to relational model, or
- designing the desired relations ad-hoc and (possibly) later testing if they are in 3NF / 4NF.

We have to choose between avoiding data redundancy (BCNF, 4NF) and ensuring dependency preservation (3NF).

There is no simple, straightforward way to enforce functional dependencies with SQL constraints.  BCNF (4NF) is therefore often preferred to 3NF.

We are likely to obtain a 4NF database schema if we come from an (E)ER model.

Although redundancy is often undesirable, some forms of redundancy can be consciously included in the design for practical reasons.  The same is the case with multivalued and composite attributes.